In [66]:
import pandas as pd
import numpy as np
import geopandas as gpd
import os
import json
from shapely.geometry import Point

Each file contains the weather data for one grid cell lat/lon in .AgMIP format.The files are named according to the following nomenclature: 
- Digits 1-4 describe location/grid cell (Corresponding to the INSI code included in the Excel spreadsheet enclosed)
- fifth digit is time period and emissions scenario:
  - 7 = 2040-2060 SSP1-RCP2.6 21st Century
  - 8 = 2040-2060 SSP3-RCP7.0 21st Century
- Sith digit is source of GCM data:
  - 1 = GFDL-ESM4 (ISIMIP)
  - 2 = IPSL-CM6A-LR (ISIMIP)
  - 3 = MPI-ESM1-2-HR (ISIMIP)
  - 4 = MRI-ESM2-0 (ISIMIP)
- Seventh Digit is downscaling/scenario methodology
  - X = no additional downscaling
- Eighth Digit is Type of Scenario:
  - 1 = Lange et al., 2020 (ISIMIP Bias-adjustment)

Inside each .AgMIP file will be a summary header containing the: location code (INSI), latitude (LAT), longitude (LONG), elevation (ELEV, m), average temperature (TAV, degC), long-term temperature amplitude (AMP, degC), reference height (REFHT, m), and wind speed height measurement (WNDHT, m).

Below this summary header, there will be the daily data for:
- DATE (yyyyddd),
- year (YYYY),
- month (MM),
- day (DD),
- solar radiation (SRAD, MJ/m2),
- **maximum air temperature (TMAX, degC),**
- **minimum air temperature (TMIN, degC)**,
- **precipitation (RAIN, mm),**
- windspeed (WIND, km/d),
- dew point temperature (DEWP, degC),
- vapor pressure (VPRS),
- relative humidity (RHUM, %)

The data needed to make the temperature and precipitation maps will be the DATE, TMAX, TMIN, and RAIN.

In [51]:
def agmip_to_df(file_path):
    with open(file_path) as f:
        lines = f.readlines()
    lat = float(lines[3][14:20])
    lon = float(lines[3][24:29])
    with open("temp.txt", "w") as f:
        f.writelines(lines[4:])
        f.close()
    working_df = pd.read_csv("temp.txt", sep="\s+", skiprows=0)
    os.remove("temp.txt")
    return [working_df, lat, lon]

test_df, test_lat, test_long = agmip_to_df("./unsynced-data/weather-data/MRI-ESM2-0-historical/BZJI84X1.AgMIP")

In [85]:
empty_grid = gpd.read_file("./synced-data/empty-grid.geojson")
weather_grid = empty_grid.copy()
# add empty columns for tmax, tmin, rain for each scenario and model
# weather_grid["tmax_historical_ipsl"] = np.nan
weather_grid["tmax_historical_mri"] = np.nan
# weather_grid["tmax_historical_mpi"] = np.nan
# weather_grid["tmax_historical_gfdl"] = np.nan
# weather_grid["tmin_historical_ipsl"] = np.nan
weather_grid["tmin_historical_mri"] = np.nan
# weather_grid["tmin_historical_mpi"] = np.nan
# weather_grid["tmin_historical_gfdl"] = np.nan
# weather_grid["rain_historical_ipsl"] = np.nan
weather_grid["rain_historical_mri"] = np.nan
# weather_grid["rain_historical_mpi"] = np.nan
# weather_grid["rain_historical_gfdl"] = np.nan
# weather_grid["tmax_ssp126_ipsl"] = np.nan
weather_grid["tmax_ssp126_mri"] = np.nan
# weather_grid["tmax_ssp126_mpi"] = np.nan
# weather_grid["tmax_ssp126_gfdl"] = np.nan
# weather_grid["tmin_ssp126_ipsl"] = np.nan
weather_grid["tmin_ssp126_mri"] = np.nan
# weather_grid["tmin_ssp126_mpi"] = np.nan
# weather_grid["tmin_ssp126_gfdl"] = np.nan
# weather_grid["rain_ssp126_ipsl"] = np.nan
weather_grid["rain_ssp126_mri"] = np.nan
# weather_grid["rain_ssp126_mpi"] = np.nan
# weather_grid["rain_ssp126_gfdl"] = np.nan
# weather_grid["tmax_ssp370_ipsl"] = np.nan
weather_grid["tmax_ssp370_mri"] = np.nan
# weather_grid["tmax_ssp370_mpi"] = np.nan
# weather_grid["tmax_ssp370_gfdl"] = np.nan
# weather_grid["tmin_ssp370_ipsl"] = np.nan
weather_grid["tmin_ssp370_mri"] = np.nan
# weather_grid["tmin_ssp370_mpi"] = np.nan
# weather_grid["tmin_ssp370_gfdl"] = np.nan
# weather_grid["rain_ssp370_ipsl"] = np.nan
weather_grid["rain_ssp370_mri"] = np.nan
# weather_grid["rain_ssp370_mpi"] = np.nan
# weather_grid["rain_ssp370_gfdl"] = np.nan


In [89]:
# This takes an a dataframe from the agmip file and joins data from that point
def weather_point_to_grid(df, lat, lon, tmax_col, tmin_col, tavg_col, rain_col):
    geometry_point = Point(lon, lat)
    matching_row = weather_grid[weather_grid.geometry.contains(geometry_point)]
    weather_grid.loc[matching_row.index, tmax_col] = df["TMAX"].mean()
    weather_grid.loc[matching_row.index, tmin_col] = df["TMIN"].mean()
    weather_grid.loc[matching_row.index, tavg_col] = (df["TMAX"].mean()+df["TMIN"].mean())/2
    weather_grid.loc[matching_row.index, rain_col] = df["RAIN"].mean()
    return weather_grid


In [87]:
# make lists of file names
historic_mri_files = os.listdir("./unsynced-data/weather-data/MRI-ESM2-0-historical")
ssp126_mri_files = os.listdir("./unsynced-data/weather-data/MRI-ESM2-0-ssp126")
ssp370_mri_files = os.listdir("./unsynced-data/weather-data/MRI-ESM2-0-ssp370")

In [90]:
for f in historic_mri_files:
    df, lat, lon = agmip_to_df("./unsynced-data/weather-data/MRI-ESM2-0-historical/"+f)
    weather_grid = weather_point_to_grid(df, lat, lon, "tmax_historical_mri", "tmin_historical_mri", "tavg_historical_mri", "rain_historical_mri")

In [91]:
for f in ssp126_mri_files:
    df, lat, lon = agmip_to_df("./unsynced-data/weather-data/MRI-ESM2-0-ssp126/"+f)
    weather_grid = weather_point_to_grid(df, lat, lon, "tmax_ssp126_mri", "tmin_ssp126_mri", "tavg_ssp126_mri", "rain_ssp126_mri")

In [92]:
for f in ssp370_mri_files:
    df, lat, lon = agmip_to_df("./unsynced-data/weather-data/MRI-ESM2-0-ssp370/"+f)
    weather_grid = weather_point_to_grid(df, lat, lon, "tmax_ssp370_mri", "tmin_ssp370_mri", "tavg_ssp370_mri", "rain_ssp370_mri")

In [93]:
weather_grid

geometry  tmax_historical_mri  tmin_historical_mri   
0      POINT (19.25000 -34.25000)            22.260035            12.175732  \
1      POINT (19.75000 -34.25000)            22.684567            11.901734   
2      POINT (20.25000 -34.25000)            24.107237            12.736351   
3      POINT (20.75000 -34.25000)            24.156037            12.986338   
4      POINT (21.25000 -34.25000)            23.694990            13.329853   
...                           ...                  ...                  ...   
10230    POINT (9.25000 36.75000)            24.534197            12.432673   
10231    POINT (9.75000 36.75000)            24.709939            13.246646   
10232   POINT (10.25000 36.75000)                  NaN                  NaN   
10233   POINT (10.75000 36.75000)                  NaN                  NaN   
10234    POINT (9.75000 37.25000)            24.656521            14.105084   

       rain_historical_mri  tmax_ssp126_mri  tmin_ssp126_mri  rain_ssp126_mri   
0                 2.187898        23.078116        12.958058         2.225379  \
1                 1.258301        23.488447        12.651752         1.253951   
2                 1.429561        24.916874        13.504654         1.397043   
3                 1.491576        24.983282        13.738310         1.399306   
4                 1.447121        24.491586        14.072541         1.412612   
...                    ...              ...              ...              ...   
10230             2.038003        25.993174        13.539651         1.986320   
10231             1.734909        26.190290        14.377012         1.724831   
10232                  NaN              NaN              NaN              NaN   
10233                  NaN              NaN              NaN              NaN   
10234             2.123145        25.954791        15.134532         1.988748   

       tmax_ssp370_mri  tmin_ssp370_mri  rain_ssp370_mri  tavg_historical_mri   
0            23.506260        13.267312         2.126054            17.217884  \
1            23.949243        12.967686         1.153294            17.293150   
2            25.377085        13.846368         1.322942            18.421794   
3            25.446769        14.093703         1.338638            18.571187   
4            24.942398        14.418753         1.322103            18.512421   
...                ...              ...              ...                  ...   
10230        26.477204        14.013807         1.850511            18.483435   
10231        26.651451        14.850301         1.605804            18.978292   
10232              NaN              NaN              NaN                  NaN   
10233              NaN              NaN              NaN                  NaN   
10234        26.293712        15.485937         1.944196            19.380802   

       tavg_ssp126_mri  tavg_ssp370_mri  
0            18.018087        18.386786  
1            18.070099        18.458464  
2            19.210764        19.611727  
3            19.360796        19.770236  
4            19.282063        19.680576  
...                ...              ...  
10230        19.766413        20.245506  
10231        20.283651        20.750876  
10232              NaN              NaN  
10233              NaN              NaN  
10234        20.544661        20.889825  

[10235 rows x 13 columns]

In [94]:
weather_grid.explore()